### Урок 9. Python применение продвинутых методов
Проанализируйте результаты эксперимента и напишите свои рекомендации менеджеру.

Mobile Games AB Testing with Cookie Cats

In [73]:
import scipy.stats as s
import numpy as np
import pandas as pd
import plotly.express as px
from statsmodels.stats.contingency_tables import mcnemar
import warnings
warnings.filterwarnings('ignore')
warnings.warn('DelftStack')
warnings.warn('Do not show this message')

In [4]:
df = pd.read_excel('результаты А_B.xlsx')
df.head(10)

userid  version  sum_gamerounds  retention_1  retention_7
0     116  gate_30               3            0            0
1     337  gate_30              38            1            0
2     377  gate_40             165            1            0
3     483  gate_40               1            0            0
4     488  gate_40             179            1            1
5     540  gate_40             187            1            1
6    1066  gate_30               0            0            0
7    1444  gate_40               2            0            0
8    1574  gate_40             108            1            1
9    1587  gate_40             153            1            0

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90189 entries, 0 to 90188
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   userid          90189 non-null  int64 
 1   version         90189 non-null  object
 2   sum_gamerounds  90189 non-null  int64 
 3   retention_1     90189 non-null  int64 
 4   retention_7     90189 non-null  int64 
dtypes: int64(4), object(1)
memory usage: 3.4+ MB


In [8]:
df.isna().sum()

userid            0
version           0
sum_gamerounds    0
retention_1       0
retention_7       0
dtype: int64

In [9]:
df.describe()

userid  sum_gamerounds   retention_1   retention_7
count  9.018900e+04    90189.000000  90189.000000  90189.000000
mean   4.998412e+06       51.872457      0.445210      0.186065
std    2.883286e+06      195.050858      0.496992      0.389161
min    1.160000e+02        0.000000      0.000000      0.000000
25%    2.512230e+06        5.000000      0.000000      0.000000
50%    4.995815e+06       16.000000      0.000000      0.000000
75%    7.496452e+06       51.000000      1.000000      0.000000
max    9.999861e+06    49854.000000      1.000000      1.000000

In [12]:
df.shape

(90189, 5)

In [13]:
df_new = df.drop_duplicates(subset=['userid'], keep=False).sort_values('userid')
df_new.head(100)

userid  version  sum_gamerounds  retention_1  retention_7
0      116  gate_30               3            0            0
1      337  gate_30              38            1            0
2      377  gate_40             165            1            0
3      483  gate_40               1            0            0
4      488  gate_40             179            1            1
..     ...      ...             ...          ...          ...
95    9443  gate_40               3            0            0
96    9589  gate_30               8            0            0
97    9699  gate_40               8            0            0
98    9828  gate_40               1            0            0
99    9831  gate_40               3            0            0

[100 rows x 5 columns]

In [14]:
df_new.shape

(90189, 5)

In [19]:
df_new.version.value_counts()

version
gate_40    45489
gate_30    44700
Name: count, dtype: int64

In [17]:
df_A = df_new.loc[df['version'] == 'gate_30']
df_A.head(10)

userid  version  sum_gamerounds  retention_1  retention_7
0      116  gate_30               3            0            0
1      337  gate_30              38            1            0
6     1066  gate_30               0            0            0
11    2101  gate_30               0            0            0
13    2179  gate_30              39            1            0
14    2218  gate_30             305            1            1
15    2382  gate_30              73            1            0
16    2392  gate_30              14            1            0
17    2451  gate_30             204            1            1
18    2482  gate_30             108            1            1

In [20]:
df_A.shape

(44700, 5)

In [47]:
df_A.describe()

userid  sum_gamerounds   retention_1   retention_7
count  4.470000e+04    44700.000000  44700.000000  44700.000000
mean   4.987564e+06       52.456264      0.448188      0.190201
std    2.881026e+06      256.716423      0.497314      0.392464
min    1.160000e+02        0.000000      0.000000      0.000000
25%    2.505469e+06        5.000000      0.000000      0.000000
50%    4.983631e+06       17.000000      0.000000      0.000000
75%    7.481497e+06       50.000000      1.000000      0.000000
max    9.999710e+06    49854.000000      1.000000      1.000000

In [48]:
df_A = df_A.loc[df_A['sum_gamerounds'] != 49854.000000] # Удалила выброс (ошибка данных - столько играть нельзя)
df_A.describe()

userid  sum_gamerounds   retention_1   retention_7
count  4.469900e+04    44699.000000  44699.000000  44699.000000
mean   4.987532e+06       51.342111      0.448198      0.190183
std    2.881051e+06      102.057598      0.497315      0.392450
min    1.160000e+02        0.000000      0.000000      0.000000
25%    2.505463e+06        5.000000      0.000000      0.000000
50%    4.983630e+06       17.000000      0.000000      0.000000
75%    7.481522e+06       50.000000      1.000000      0.000000
max    9.999710e+06     2961.000000      1.000000      1.000000

In [49]:
fig = px.scatter(df_A, x='sum_gamerounds', y='userid', marginal_x="box", template="simple_white")
fig.show()

In [18]:
df_B = df_new.loc[df['version'] == 'gate_40']
df_B.head(10)

userid  version  sum_gamerounds  retention_1  retention_7
2      377  gate_40             165            1            0
3      483  gate_40               1            0            0
4      488  gate_40             179            1            1
5      540  gate_40             187            1            1
7     1444  gate_40               2            0            0
8     1574  gate_40             108            1            1
9     1587  gate_40             153            1            0
10    1842  gate_40               3            0            1
12    2132  gate_40              30            1            0
19    2502  gate_40               1            0            0

In [21]:
df_B.shape

(45489, 5)

In [23]:
df_B.describe()

userid  sum_gamerounds   retention_1   retention_7
count  4.548900e+04    45489.000000  45489.000000  45489.000000
mean   5.009073e+06       51.298776      0.442283      0.182000
std    2.885496e+06      103.294416      0.496663      0.385849
min    3.770000e+02        0.000000      0.000000      0.000000
25%    2.517171e+06        5.000000      0.000000      0.000000
50%    5.007329e+06       16.000000      0.000000      0.000000
75%    7.510762e+06       52.000000      1.000000      0.000000
max    9.999861e+06     2640.000000      1.000000      1.000000

In [46]:
fig = px.scatter(df_B, x='sum_gamerounds', y='userid', marginal_x="box", template="simple_white")
fig.show()

Данные в датафрейме качественного характера и зависимые (т.к. сравниваем удержание игрока через 1 день и 7 дней в обоих группах соответственно), поэтому применяю критерий Мак-Немара

In [66]:
df_A['retention_1'].value_counts()

retention_1
0    24665
1    20034
Name: count, dtype: int64

In [67]:
df_B['retention_1'].value_counts()

retention_1
0    25370
1    20119
Name: count, dtype: int64

In [70]:
retention1 = [[df_A['retention_1'].value_counts()[0], df_A['retention_1'].value_counts()[1]], [df_B['retention_1'].value_counts()[0], df_B['retention_1'].value_counts()[1]]]
retention1

[[24665, 20034], [25370, 20119]]

In [87]:
print(mcnemar(retention1, exact=False))

pvalue      2.4012360487243992e-138
statistic   626.866025019822


По резутьтатам теста, можно сделать вывод, что между группой А и группой В нет статистически значимой разницы на удержание игрока на 1 день, т.к. pvalue < 0.05

In [88]:
retention7 = [[df_A['retention_7'].value_counts()[0], df_A['retention_7'].value_counts()[1]], [df_B['retention_7'].value_counts()[0], df_B['retention_7'].value_counts()[1]]]
retention7

[[36198, 8501], [37210, 8279]]

In [89]:
print(mcnemar(retention7, exact=False))

pvalue      0.0
statistic   18029.56102469865


По резутьтатам теста, можно сделать вывод, что между группой А и группой В нет статистически значимой разницы на удержание игрока на 7 день, т.к. pvalue < 0.05

### Рекомендация
Оставить версию игры gate_30 из контрольной группы, т.к. нет разницы между тестовыми группами на удержание игрока на следующий день и седьмой.